In [1]:
from matplotlib import pyplot as plt
import numpy as np
import math,random
from tqdm import tqdm
from random import shuffle
import pprint

import pandas as pd
from src.features.build_features import word_count_series
from src.data.make_dataset import create_dataset
from src.data.util import unzip_file

def step_function(x):
    return 1 if x >= 0 else 0


def perceptron_output(weights, bias, x):
    '''Returns 1 if the perceptrion 'fires', 0 if not '''
    return step_function(np.dot(weights, x) + bias)

def sigmoid(t):
    return 1 / (1 + math.exp(-t))

def neuron_output(weights, inputs):
    return sigmoid(np.dot(weights, inputs))

def predict(input, network):
    return feed_forward(network, input)[-1]

def feed_forward(neural_network, input_vector):
    """takes in a neural network (represented as a list of lists of lists of weights)
    and returns the output from forward-propagating the input"""

    outputs = []

    for layer in neural_network:

        input_with_bias = input_vector + [1]             # add a bias input
        output = [neuron_output(neuron, input_with_bias) # compute the output
                  for neuron in layer]                   # for this layer
        outputs.append(output)                           # and remember it

        # the input to the next layer is the output of this one
        input_vector = output

    return outputs
    
def backpropagate(network, input_vector, targets):
    hidden_outputs, outputs = feed_forward(network, input_vector)
    # the output * (1 - output) is from the derivative of sigmoid
    output_deltas = [output * (1 - output) * (output - target) for output, target in zip(outputs, targets)]
        # adjust weights for output layer, one neuron at a time
    for i, output_neuron in enumerate(network[-1]):
    # focus on the ith output layer neuron
        for j, hidden_output in enumerate(hidden_outputs + [1]):
            # adjust the jth weight based on both
            # this neuron's delta and its jth input
            output_neuron[j] -= output_deltas[i] * hidden_output
    # back-propagate errors to hidden layer
    hidden_deltas = [hidden_output * (1 - hidden_output) * np.dot(output_deltas, [n[i] for n in output_layer])for i, hidden_output in enumerate(hidden_outputs)]
        
    # adjust weights for hidden layer, one neuron at a time
    for i, hidden_neuron in enumerate(network[0]):
        for j, input in enumerate(input_vector + [1]):
            hidden_neuron[j] -= hidden_deltas[i] * input

In [2]:
# Importing data
df = create_dataset()

Skipping unzip...


In [3]:
# targets
series = df['genre'].value_counts()
genre_labels = series.keys() # getting genre labels
targets = [[1 if i == j else 0 for i in genre_labels] for j in df['genre']]

# features
features_series = word_count_series(df['lyrics'])
inputs = [[feature] for feature in features_series]
shuffle(inputs)
inputs = inputs[0:500]

In [ ]:
########### Træning af model ###########

###########
# Opsætning af Neural Network
###########
random.seed(0) # to get repeatable results
input_size = 1 # antal af input noder (samme antal som feautures)
num_hidden = 5 # antal af hidden noder
output_size = 12 # antal af output noder (i vores tilfælde, genres)

# each hidden neuron has one weight per input, plus a bias weight
hidden_layer = [[random.random() for __ in range(input_size + 1)] for __ in range(num_hidden)]

# each output neuron has one weight per hidden neuron, plus a bias weight
output_layer = [[random.random() for __ in range(num_hidden + 1)] for __ in range(output_size)]

# the network starts out with random weights
network = [hidden_layer, output_layer]

# Iteration of training
for __ in  tqdm(range(1000)):
    for input_vector, target_vector in zip(inputs, targets):
        backpropagate(network, input_vector, target_vector)



  0%|          | 0/1000 [00:00<?, ?it/s]

1
 
[[0.8755939452607421, 0.47216791588279716, 0.24931890446511076, 0.7232852642226308, 0.5858500567407385, 0.21798740142784748], [0.909836005975687, 0.9828752260451, 0.8103069860040365, 0.9022557004470296, 0.31023731932677956, 0.7299214982675756], [0.8627035209425696, 0.6478491648900174, 0.43600794842728946, 0.0645664410429419, 0.3980370684283598, 0.5747522064183778], [0.8998223694945446, 0.9534176840274052, 0.46382109280936346, 0.8521212440282865, 0.24730362664860586, 0.7918391432696688], [0.51171229689058, -0.022945306780990396, 0.6827176794589448, 0.3618365352792594, 0.7878579702032237, 0.6311661942868415], [-0.04971709257576652, 0.44271795457512986, 0.8167428636025861, 0.1930509649969372, 0.2743444508571953, 0.8196113202184598], [0.15541298710885187, 0.5318566362271332, 0.20296182422168152, 0.9318861458966047, 0.7675253648863314, 0.4123154670420317], [0.015740076903934766, 0.2553488630239451, 0.44323490087197326, 0.8681280825783061, 0.04435210428250304, 0.48656150444195057], [0.69

[[-0.3141162689555299, -0.717542298333475, -0.9403913097511615, -0.4664249499936411, -0.6038601574755337, -0.9717228127884249], [-0.32674653652490687, -0.25370731645549444, -0.42627555649655735, -0.3343268420535643, -0.926345223173815, -0.5066610442330183], [0.8604830493627249, 0.6456286933101728, 0.43378747684744573, 0.06234596946309683, 0.39581659684851594, 0.5725317348385343], [-0.46791601516868175, -0.41432070063582127, -0.9039172918538633, -0.5156171406349398, -1.1204347580146197, -0.575899241393558], [-0.6495894085612411, -1.1842470122328104, -0.4785840259928766, -0.7994651701725618, -0.3734437352485974, -0.5301355111649798], [-1.1355746192819052, -0.6431395721310058, -0.26911466310355114, -0.8928065617091987, -0.8115130758489406, -0.26624620648767733], [-1.0140933807566175, -0.6376497316383354, -0.9665445436437872, -0.23762022196886395, -0.4019810029791373, -0.757190900823437], [-1.0065221241680704, -0.7669133380480605, -0.5790273002000317, -0.15413411849369885, -0.9779100967895



  0%|          | 1/1000 [00:00<07:54,  2.11it/s]


 
[[-0.2384496841222072, -0.6418757135001523, -0.8647247249178388, -0.39075836516031853, -0.528193572642211, -0.8960562279551022], [-0.46795215471448626, -0.3949129346450738, -0.5674811746861363, -0.47553246024314366, -1.0675508413633943, -0.6478666624225976], [-0.2414645968727258, -0.45631895292527835, -0.668160169388005, -1.0396016767723537, -0.7061310493869348, -0.5294159113969166], [-0.3824832633149084, -0.32888794878204786, -0.81848454000009, -0.43018438878116655, -1.035002006160846, -0.49046648953978494], [-0.6311471290194185, -1.1658047326909893, -0.4601417464510549, -0.7810228906307392, -0.3550014557067757, -0.5116932316231573], [-1.1774352462386815, -0.685000199087783, -0.31097529006032776, -0.9346671886659759, -0.8533737028057178, -0.308106833444454], [-1.056168861234302, -0.67972521211602, -1.008620024121472, -0.27969570244654834, -0.44405648345682164, -0.7992663813011216], [-1.048265600577679, -0.8086568144576682, -0.6207707766096394, -0.19587759490330672, -1.0196535731991

...


 
[[-0.23355129006867975, -0.6369773194466286, -0.8598263308643154, -0.385859971106792, -0.5232951785886881, -0.8911578339015788], [-0.2931726132071878, -0.22013339313777508, -0.3927016331788332, -0.300752918735845, -0.8927712998561023, -0.4730871209152935], [-0.08492310097103553, -0.29977745702358466, -0.5116186734863097, -0.88306018087066, -0.5495895534852393, -0.3728744154952218], [-0.2804915529535128, -0.22689623842065143, -0.7164928296386858, -0.3281926784197694, -0.9330102957994557, -0.38847477917838874], [-0.7240368597974307, -1.2586944634689898, -0.5530314772290654, -0.8739126214087514, -0.44789118648478304, -0.6045829624011694], [-1.1531828686194823, -0.66074782146859, -0.28672291244113474, -0.9104148110467791, -0.8291213251865208, -0.28385445582526114], [-1.2798155240296207, -0.9033718749113322, -1.2322666869167906, -0.5033423652418628, -0.6677031462521342, -1.022913044096436], [-1.2714265018728987, -1.0318177157528872, -0.8439316779048521, -0.4190384961985256, -1.2428144744

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



1
 
[[-0.20243185645439624, -0.6058578858323445, -0.8287068972500314, -0.35474053749250806, -0.4921757449744043, -0.8600384002872948], [0.5770771469745888, 0.6501163670440016, 0.47754812700294363, 0.5694968414459316, -0.022521539674326855, 0.3971626392664835], [-0.276687917490274, -0.49154227354282304, -0.7033834900055482, -1.074824997389898, -0.7413543700044778, -0.5646392320144604], [-0.4275056008280205, -0.37391028629515927, -0.8635068775131928, -0.47520672629427724, -1.0800243436739632, -0.5354888270528969], [-0.7447173734327959, -1.2793749771043537, -0.5737119908644306, -0.8945931350441165, -0.46857170012014737, -0.6252634760365345], [-0.9322269496794223, -0.43979190252852973, -0.0657669935010745, -0.6894588921067187, -0.6081654062464603, -0.06289853688520085], [-1.2821971880417606, -0.9057535389234707, -1.2346483509289305, -0.5057240292540013, -0.6700848102642727, -1.025294708108576], [-1.2738071323959925, -1.034198346275981, -0.8463123084279464, -0.4214191267216203, -1.245195105

ERROR:tornado.general:Uncaught exception in ZMQStream callback
Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py", line 2963, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-8-c4318fb22684>", line 23, in <module>
    backpropagate(network, input_vector, target_vector)
  File "<ipython-input-7-dd4b9b27382f>", line 65, in backpropagate
    print(output_layer)
KeyboardInterrupt

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py", line 1863, in showtraceback
    stb = value._render_traceback_()
AttributeError: 'KeyboardInterrupt' object has no attribute '_render_traceback_'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/IPython/core/ultratb.py", line 



Exception ignored in: <bound method tqdm.__del__ of   1%|▏         | 13/1000 [00:07<09:11,  1.79it/s]>
Traceback (most recent call last):
  File "/Users/Mellem/.local/lib/python3.6/site-packages/tqdm/_tqdm.py", line 931, in __del__
    self.close()
  File "/Users/Mellem/.local/lib/python3.6/site-packages/tqdm/_tqdm.py", line 1133, in close
    self._decr_instances(self)
  File "/Users/Mellem/.local/lib/python3.6/site-packages/tqdm/_tqdm.py", line 496, in _decr_instances
    cls.monitor.exit()
  File "/Users/Mellem/.local/lib/python3.6/site-packages/tqdm/_monitor.py", line 52, in exit
    self.join()
  File "/anaconda3/lib/python3.6/threading.py", line 1053, in join
    raise RuntimeError("cannot join current thread")
RuntimeError: cannot join current thread


In [22]:
# denne blok er forbeholdt for egentlige predicts fra trænet model

network

[[[0.8444218515250481, 0.7579544029403025],
  [0.4205715808309005, 0.25891675029296335],
  [0.5112747213686085, 0.4049341374504143],
  [0.7837985890347726, 0.30331272607892745],
  [0.4765969541523558, 0.5833820394550312]],
 [[-0.1538539397805636,
   -0.5572799691578535,
   -0.780128980575759,
   -0.30616262081801743,
   -0.44359782830013267,
   -0.8114604836130224],
  [-0.48858790774036187,
   -0.41554868767084685,
   -0.5881169277115286,
   -0.49616821326896754,
   -1.0881865943900944,
   -0.6685024154479802],
  [-0.26140879068556466,
   -0.47626314673789444,
   -0.6881043632001824,
   -1.0595458705843126,
   -0.7260752431993314,
   -0.5493601052093133],
  [-0.4087079858816599,
   -0.3551126713486191,
   -0.8447092625656373,
   -0.45640911134761797,
   -1.061226728727982,
   -0.5166912121062774],
  [-0.7429046243611146,
   -1.277562228031674,
   -0.57189924179275,
   -0.892780385972435,
   -0.46675895104838894,
   -0.6234507269648537],
  [-0.09242814606119928,
   0.40000690108915987,


In [24]:
pprint.pprint([[[0.8444218515250481, 0.7579544029403025], [0.420571580830845, 0.25891675029296335], [0.5112747213686085, 0.4049341374504143], [0.7837985890347726, 0.30331272607892745], [0.4765969541523558, 0.5833820394550312]], [[0.9081128851953352, 0.5046868558173903, 0.28183784439970383, 0.7558042041572239, 0.6183689966753316, 0.25050634136244054], [0.9097462559682401, 0.9827854760376531, 0.8102172359965896, 0.9021659504395827, 0.3101475693193326, 0.7298317482601286], [0.8988382879679935, 0.6839839319154413, 0.47214271545271336, 0.1007012080683658, 0.4341718354537837, 0.6108869734438016], [0.9130110532378982, 0.9666063677707588, 0.47700977655271704, 0.8653099277716401, 0.2604923103919594, 0.8050278270130223], [0.5486993038355893, 0.014041700164018955, 0.7197046864039541, 0.39882354222426875, 0.824844977148233, 0.6681532012318508], [0.0011428193144282783, 0.49357786646532464, 0.8676027754927809, 0.24391087688713198, 0.32520436274739006, 0.8704712321086546], [0.19106709150239054, 0.5675107406206719, 0.23861592861522019, 0.9675402502901433, 0.80317946927987, 0.44796957143557037], [0.08044581855253541, 0.32005460467254576, 0.5079406425205739, 0.9328338242269067, 0.10905784593110368, 0.5512672460905512], [0.7065614098668896, 0.5474409113284238, 0.814466863291336, 0.540283606970324, 0.9638385459738009, 0.603185627961383], [0.5876170641754364, 0.4449890262755162, 0.5962868615831063, 0.38490114597266045, 0.5756510141648885, 0.290329502402758], [0.18939132855435614, 0.1867295282555551, 0.6127731798686067, 0.6566593889896288, 0.47653099200938076, 0.08982436119559367], [0.7576039219664368, 0.8767703708227748, 0.9233810159462806, 0.8424602231401824, 0.898173121357879, 0.9230824398201768]]])

[[[0.8444218515250481, 0.7579544029403025],
  [0.420571580830845, 0.25891675029296335],
  [0.5112747213686085, 0.4049341374504143],
  [0.7837985890347726, 0.30331272607892745],
  [0.4765969541523558, 0.5833820394550312]],
 [[0.9081128851953352,
   0.5046868558173903,
   0.28183784439970383,
   0.7558042041572239,
   0.6183689966753316,
   0.25050634136244054],
  [0.9097462559682401,
   0.9827854760376531,
   0.8102172359965896,
   0.9021659504395827,
   0.3101475693193326,
   0.7298317482601286],
  [0.8988382879679935,
   0.6839839319154413,
   0.47214271545271336,
   0.1007012080683658,
   0.4341718354537837,
   0.6108869734438016],
  [0.9130110532378982,
   0.9666063677707588,
   0.47700977655271704,
   0.8653099277716401,
   0.2604923103919594,
   0.8050278270130223],
  [0.5486993038355893,
   0.014041700164018955,
   0.7197046864039541,
   0.39882354222426875,
   0.824844977148233,
   0.6681532012318508],
  [0.0011428193144282783,
   0.49357786646532464,
   0.8676027754927809,
   0